In [1]:
import pandas as pd
import numpy as np
import calendar
import matplotlib.pyplot as plt
from sklearn.svm import SVR
import seaborn as  sns
from sklearn.preprocessing import StandardScaler,Normalizer
from sklearn.metrics import r2_score, mean_squared_error,accuracy_score
from sklearn.linear_model import LinearRegression,Lasso,Ridge,ElasticNet
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor,GradientBoostingRegressor
from sklearn.model_selection import train_test_split
import pandas_profiling

C:\Users\SURBHI\Anaconda3\lib\site-packages\sklearn\ensemble\weight_boosting.py:29: DeprecationWarning: numpy.core.umath_tests is an internal NumPy module and should not be imported. It will be removed in a future NumPy release.
  from numpy.core.umath_tests import inner1d


In [2]:
df=pd.read_csv("C:/Users/SURBHI/Downloads/train (1).csv")
df.dropna(inplace=True)
df.head()

Year  Month ProductCategory  Sales(In ThousandDollars)
0  2009      1   WomenClothing                     1755.0
1  2009      1     MenClothing                      524.0
2  2009      1   OtherClothing                      936.0
3  2009      2   WomenClothing                     1729.0
4  2009      2     MenClothing                      496.0

In [3]:
df.shape

(170, 4)

In [4]:
test=pd.read_csv("C:/Users/SURBHI/Downloads/walmart-sales-prediction/test (3).csv")
test.head()

Year  Month ProductCategory
0  2014      1   WomenClothing
1  2014      1     MenClothing
2  2014      1   OtherClothing
3  2014      2   WomenClothing
4  2014      2     MenClothing

In [5]:
eventtest=pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/Events_HolidaysData.xlsx")
eventtest.head()
etest=eventtest[eventtest.Year== 2014]
etest.reset_index(inplace=True)

etest.head()
etest["MonthDate"]=etest["MonthDate"].astype('datetime64[ns]')
etest["Month"]= etest["MonthDate"].dt.month
etest.drop(["index","MonthDate"],axis=1,inplace=True)
etest.head()

C:\Users\SURBHI\Anaconda3\lib\site-packages\ipykernel_launcher.py:7: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  import sys
C:\Users\SURBHI\Anaconda3\lib\site-packages\ipykernel_launcher.py:8: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  
C:\Users\SURBHI\Anaconda3\lib\site-packages\pandas\core\frame.py:3697: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: http://pandas.pydata.org/pandas-docs/stable/indexing.html#indexing-view-versus-copy
  errors=errors)


Year                        Event      DayCategory  Month
0  2014               New Year's Day  Federal Holiday      1
1  2014   Martin Luther King Jr. Day  Federal Holiday      1
2  2014              Valentine's Day            Event      2
3  2014              Presidents' Day  Federal Holiday      2
4  2014  Thomas Jefferson's Birthday            Event      4

In [6]:
macrotest=pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/macro_economic.xlsx")
macrotest.head()
# macro[macro.Year== 2014]
macrotest['Year-Month']=macrotest["Year-Month"].astype('datetime64[ns]')
macrotest["Month"]=macrotest['Year-Month'].dt.month
macrotest["Year"]=macrotest["Year-Month"].dt.year
macrotest.drop(["Year-Month","AdvertisingExpenses (in Thousand Dollars)","PartyInPower"],axis=1,inplace=True)
macrotest.head()

Monthly Nominal GDP Index (inMillion$)  \
0                            14421.752895   
1                            14389.200466   
2                            14340.701639   
3                            14326.815525   
4                            14345.904809   

   Monthly Real GDP Index (inMillion$)      CPI  unemployment rate  \
0                         14407.053343  233.402                7.8   
1                         14366.176571  234.663                8.3   
2                         14351.786822  235.067                8.7   
3                         14351.601731  235.582                9.0   
4                         14368.123959  235.975                9.4   

   CommercialBankInterestRateonCreditCardPlans  \
0                                        12.03   
1                                        12.97   
2                                        12.97   
3                                        12.97   
4                                        13.32   

   Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan  \
0                                              11.44                   
1                                              11.05                   
2                                              11.05                   
3                                              11.05                   
4                                              11.25                   

   Earnings or wages  in dollars per hour  \
0                                   22.05   
1                                   22.22   
2                                   22.22   
3                                   22.13   
4                                   22.04   

   Cotton Monthly Price - US cents per Pound(lbs)  Change(in%)  \
0                                           57.70         4.02   
1                                           55.21        -4.32   
2                                           51.50        -6.72   
3                                           56.78        10.25   
4                                           61.95         9.11   

   Average upland planted(million acres)  \
0                                  9.296   
1                                  9.296   
2                                  9.296   
3                                  9.296   
4                                  9.297   

   Average upland harvested(million acres)  yieldperharvested acre  \
0                                    7.559                     799   
1                                    7.559                     799   
2                                    7.559                     799   
3                                    7.559                     787   
4                                    7.400                     803   

   Production (in  480-lb netweright in million bales)  \
0                                             12.589     
1                                             12.589     
2                                             12.589     
3                                             12.400     
4                                             12.384     

   Mill use  (in  480-lb netweright in million bales)  Exports  Month  Year  
0                                               4.17    11.550      1  2009  
1                                               3.87    11.100      2  2009  
2                                               3.72    11.650      3  2009  
3                                               3.62    12.225      4  2009  
4                                               3.52    12.300      5  2009

In [7]:
w6 = pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/WeatherData.xlsx","2014")
w6.head()
for i in range(12,22):
    w6[w6.columns[i]]=pd.to_numeric(w6[w6.columns[i]],errors='coerce')
w6["Year-Month"]=w6["Year"].astype(str) +"-"+w6["Month"].astype(str)
w6["Year-Month"]=w6["Year-Month"].astype('datetime64[ns]')
w6['Year']=w6["Year-Month"].dt.year
w6['Month']=w6["Year-Month"].dt.month
w6.drop(["Year-Month","WeatherEvent"],axis=1,inplace=True)
w6 =w6.groupby(["Year","Month"]).mean()


w6.info()

<class 'pandas.core.frame.DataFrame'>
MultiIndex: 12 entries, (2014, 1) to (2014, 12)
Data columns (total 20 columns):
Day                            12 non-null float64
Temp high (°C)                 12 non-null float64
Temp avg (°C)                  12 non-null float64
Temp low (°C)                  12 non-null float64
Dew Point high (°C)            12 non-null float64
Dew Point avg (°C)             12 non-null float64
Dew Point low (°C)             12 non-null float64
Humidity (%) high              12 non-null float64
Humidity (%) avg               12 non-null float64
Humidity (%) low               12 non-null float64
Sea Level Press. (hPa) high    12 non-null float64
Sea Level Press. (hPa) avg     12 non-null float64
Sea Level Press. (hPa) low     12 non-null float64
Visibility (km) high           12 non-null float64
Visibility (km) avg            12 non-null float64
Visibility (km) low            12 non-null float64
Wind (km/h) low                12 non-null float64
Wind (km/h) av

## combining all  test

In [8]:
testmacro=pd.merge(test,macrotest,on=["Year","Month"],how='left')
print(testmacro.shape)
testmacro.head()

(36, 18)


Year  Month ProductCategory  Monthly Nominal GDP Index (inMillion$)  \
0  2014      1   WomenClothing                            16955.608626   
1  2014      1     MenClothing                            16955.608626   
2  2014      1   OtherClothing                            16955.608626   
3  2014      2   WomenClothing                            17028.586348   
4  2014      2     MenClothing                            17028.586348   

   Monthly Real GDP Index (inMillion$)      CPI  unemployment rate  \
0                         15705.972667  259.596                6.6   
1                         15705.972667  259.596                6.6   
2                         15705.972667  259.596                6.6   
3                         15762.598920  259.019                6.7   
4                         15762.598920  259.019                6.7   

   CommercialBankInterestRateonCreditCardPlans  \
0                                        11.85   
1                                        11.85   
2                                        11.85   
3                                        11.83   
4                                        11.83   

   Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan  \
0                                              10.22                   
1                                              10.22                   
2                                              10.22                   
3                                              10.09                   
4                                              10.09                   

   Earnings or wages  in dollars per hour  \
0                                   24.35   
1                                   24.35   
2                                   24.35   
3                                   24.58   
4                                   24.58   

   Cotton Monthly Price - US cents per Pound(lbs)  Change(in%)  \
0                                           90.96         3.97   
1                                           90.96         3.97   
2                                           90.96         3.97   
3                                           94.05         3.40   
4                                           94.05         3.40   

   Average upland planted(million acres)  \
0                                 10.206   
1                                 10.206   
2                                 10.206   
3                                 10.206   
4                                 10.206   

   Average upland harvested(million acres)  yieldperharvested acre  \
0                                    7.465                     807   
1                                    7.465                     807   
2                                    7.465                     807   
3                                    7.465                     807   
4                                    7.465                     807   

   Production (in  480-lb netweright in million bales)  \
0                                             12.551     
1                                             12.551     
2                                             12.551     
3                                             12.551     
4                                             12.551     

   Mill use  (in  480-lb netweright in million bales)  Exports  
0                                               3.58      9.75  
1                                               3.58      9.75  
2                                               3.58      9.75  
3                                               3.58      9.75  
4                                               3.58      9.75

In [9]:
testmacroevent=pd.merge(testmacro,etest,on=["Year","Month"],how='left')

testmacroevent.head()
testmacroevent.drop("Event",axis=1,inplace=True)
testmacroevent.drop("DayCategory",axis=1,inplace=True)
testmacroevent.drop_duplicates(inplace=True)
# testmacroevent[testmacroevent.Month == 12]
print(testmacroevent.shape)
testmacroevent.groupby(["Year","Month"]) ["ProductCategory"].describe()

(36, 18)


count unique            top freq
Year Month                                 
2014 1         3      3  OtherClothing    1
     2         3      3  OtherClothing    1
     3         3      3  OtherClothing    1
     4         3      3  OtherClothing    1
     5         3      3  OtherClothing    1
     6         3      3  OtherClothing    1
     7         3      3  OtherClothing    1
     8         3      3  OtherClothing    1
     9         3      3  OtherClothing    1
     10        3      3  OtherClothing    1
     11        3      3  OtherClothing    1
     12        3      3  OtherClothing    1

In [46]:
finaltest=pd.merge(testmacroevent,w6,on=["Year","Month"],how='inner')
finaltest.drop_duplicates(inplace=True)
# print(finaltest.columns)

# finaltest.drop("Precip.\xa0(mm) sum",axis=1,inplace=True)

finaltest.drop("Day",axis=1,inplace=True)
print(finaltest.shape)
finaltest.groupby(["Year","Month"]) ["ProductCategory"].describe()

(36, 37)


count unique            top freq
Year Month                                 
2014 1         3      3  OtherClothing    1
     2         3      3  OtherClothing    1
     3         3      3  OtherClothing    1
     4         3      3  OtherClothing    1
     5         3      3  OtherClothing    1
     6         3      3  OtherClothing    1
     7         3      3  OtherClothing    1
     8         3      3  OtherClothing    1
     9         3      3  OtherClothing    1
     10        3      3  OtherClothing    1
     11        3      3  OtherClothing    1
     12        3      3  OtherClothing    1

In [11]:
event= pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/Events_HolidaysData.xlsx",nrows=92)
event.head()
event.tail()

Year  MonthDate             Event      DayCategory
87  2013 2011-11-01      Veterans Day  Federal Holiday
88  2013 2028-11-01  Thanksgiving Day  Federal Holiday
89  2013 2024-12-01     Christmas Eve            Event
90  2013 2025-12-01     Christmas Day  Federal Holiday
91  2013 1931-12-01    New Year's Eve            Event

In [12]:
import datetime as dt
event["MonthDate"]=event["MonthDate"].astype('datetime64[ns]')
event["Day"] =event["MonthDate"].dt.day
event["MonthDate"]=event["MonthDate"].astype('datetime64[ns]')
event["Month"]= event["MonthDate"].dt.month
event.head()

Year  MonthDate                       Event      DayCategory  Day  Month
0  2009 2001-01-01              New Year's Day  Federal Holiday    1      1
1  2009 2019-01-01  Martin Luther King Jr. Day  Federal Holiday    1      1
2  2009 2014-02-01             Valentine's Day            Event    1      2
3  2009 2016-02-01             Presidents' Day  Federal Holiday    1      2
4  2009 2012-04-01               Easter Sunday            Event    1      4

In [13]:
macro=pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/macro_economic.xlsx",nrows=60)
macro.head()
macro.tail()

Year-Month  Monthly Nominal GDP Index (inMillion$)  \
55  2013 - Aug                            16776.992565   
56  2013 - Sep                            16785.312189   
57  2013 - Oct                            16884.854816   
58  2013 - Nov                            17053.738107   
59  2013 - Dec                            17061.071077   

    Monthly Real GDP Index (inMillion$)      CPI PartyInPower  \
55                         15673.439971  257.659    Democrats   
56                         15644.832268  258.504    Democrats   
57                         15729.959366  257.069    Democrats   
58                         15841.758762  257.377    Democrats   
59                         15810.410182  257.284    Democrats   

    unemployment rate  CommercialBankInterestRateonCreditCardPlans  \
55                7.3                                        11.88   
56                7.2                                        11.88   
57                7.2                                        11.88   
58                6.9                                        11.85   
59                6.7                                        11.85   

    Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan  \
55                                              10.13                   
56                                              10.13                   
57                                              10.13                   
58                                              10.22                   
59                                              10.22                   

    Earnings or wages  in dollars per hour  \
55                                   23.80   
56                                   24.16   
57                                   24.04   
58                                   24.11   
59                                   24.30   

   AdvertisingExpenses (in Thousand Dollars)  \
55                                         ?   
56                                         ?   
57                                         ?   
58                                         ?   
59                                         ?   

    Cotton Monthly Price - US cents per Pound(lbs)  Change(in%)  \
55                                           92.71         0.10   
56                                           90.09        -2.83   
57                                           89.35        -0.82   
58                                           84.65        -5.26   
59                                           87.49         3.35   

    Average upland planted(million acres)  \
55                                 10.015   
56                                 10.136   
57                                 10.136   
58                                 10.136   
59                                 10.136   

    Average upland harvested(million acres)  yieldperharvested acre  \
55                                    7.519                     796   
56                                    7.582                     777   
57                                    7.582                     777   
58                                    7.582                     790   
59                                    7.582                     788   

    Production (in  480-lb netweright in million bales)  \
55                                             12.473     
56                                             12.273     
57                                             12.273     
58                                             12.479     
59                                             12.443     

    Mill use  (in  480-lb netweright in million bales)  Exports  
55                                               3.48     13.38  
56                                               3.48      9.65  
57                                               3.48      9.65  
58                                               3.58      9.65  
59                                               3.5

In [14]:
w1 = pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/WeatherData.xlsx","2009")
w2 = pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/WeatherData.xlsx","2010")
w3 = pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/WeatherData.xlsx","2011")
w4 = pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/WeatherData.xlsx","2012")
w5 = pd.read_excel("C:/Users/SURBHI/Downloads/walmart-sales-prediction/WeatherData.xlsx","2013")


weather =pd.DataFrame()
weather= pd.concat([w1,w2,w3,w4,w5],join='outer')
weather.head()

Year Month  Day Temp high (°C) Temp avg (°C) Temp low (°C)  \
0  2009   Jan    1             -3            -6            -9   
1  2009   Jan    2              1            -2            -5   
2  2009   Jan    3              3             1            -2   
3  2009   Jan    4              6             1            -4   
4  2009   Jan    5              6             5             3   

  Dew Point high (°C) Dew Point avg (°C) Dew Point low (°C) Humidity (%) high  \
0                 -16                -17                -19                54   
1                  -3                 -7                -17                78   
2                  -5                 -9                -13                72   
3                 -10                -12                -13                55   
4                  -1                 -5                -16                62   

      ...      Sea Level Press. (hPa) avg Sea Level Press. (hPa) low  \
0     ...                            1023                       1015   
1     ...                            1012                       1007   
2     ...                            1015                       1008   
3     ...                            1017                       1015   
4     ...                            1014                       1013   

  Visibility (km) high Visibility (km) avg Visibility (km) low  \
0                   16                  16                  16   
1                   16                  13                   2   
2                   16                  16                  16   
3                   16                  16                  16   
4                   16                  16                  16   

  Wind (km/h) low Wind (km/h) avg Wind (km/h) high Precip. (mm) sum  \
0              37              18               60                0   
1              27              10               48                T   
2              27              16               42                T   
3              32              12               40                0   
4              23              11               34                T   

  WeatherEvent  
0          NaN  
1         Snow  
2          NaN  
3          NaN  
4          NaN  

[5 rows x 23 columns]

In [15]:
weather["Year-Month"]=weather["Year"].astype(str) +"-"+weather["Month"].astype(str)
weather.head()

Year Month  Day Temp high (°C) Temp avg (°C) Temp low (°C)  \
0  2009   Jan    1             -3            -6            -9   
1  2009   Jan    2              1            -2            -5   
2  2009   Jan    3              3             1            -2   
3  2009   Jan    4              6             1            -4   
4  2009   Jan    5              6             5             3   

  Dew Point high (°C) Dew Point avg (°C) Dew Point low (°C) Humidity (%) high  \
0                 -16                -17                -19                54   
1                  -3                 -7                -17                78   
2                  -5                 -9                -13                72   
3                 -10                -12                -13                55   
4                  -1                 -5                -16                62   

     ...     Sea Level Press. (hPa) low Visibility (km) high  \
0    ...                           1015                   16   
1    ...                           1007                   16   
2    ...                           1008                   16   
3    ...                           1015                   16   
4    ...                           1013                   16   

  Visibility (km) avg Visibility (km) low Wind (km/h) low Wind (km/h) avg  \
0                  16                  16              37              18   
1                  13                   2              27              10   
2                  16                  16              27              16   
3                  16                  16              32              12   
4                  16                  16              23              11   

  Wind (km/h) high Precip. (mm) sum WeatherEvent Year-Month  
0               60                0          NaN   2009-Jan  
1               48                T         Snow   2009-Jan  
2               42                T          NaN   2009-Jan  
3               40                0          NaN   2009-Jan  
4               34                T          NaN   2009-Jan  

[5 rows x 24 columns]

In [16]:
weather["Year-Month"]=weather["Year-Month"].astype('datetime64[ns]')
weather['Year']=weather["Year-Month"].dt.year
weather['Month']=weather["Year-Month"].dt.month

In [17]:
weather.drop('Year-Month',axis=1,inplace=True)

In [18]:
weather.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 1826 entries, 0 to 364
Data columns (total 23 columns):
Year                           1826 non-null int64
Month                          1826 non-null int64
Day                            1826 non-null int64
Temp high (°C)                 1826 non-null object
Temp avg (°C)                  1826 non-null object
Temp low (°C)                  1826 non-null object
Dew Point high (°C)            1826 non-null object
Dew Point avg (°C)             1826 non-null object
Dew Point low (°C)             1826 non-null object
Humidity (%) high              1826 non-null object
Humidity (%) avg               1826 non-null object
Humidity (%) low               1826 non-null object
Sea Level Press. (hPa) high    1826 non-null object
Sea Level Press. (hPa) avg     1826 non-null object
Sea Level Press. (hPa) low     1826 non-null object
Visibility (km) high           1826 non-null object
Visibility (km) avg            1826 non-null object
Visibility (k

In [19]:
for i in range(2,22):
    weather[weather.columns[i]]=pd.to_numeric(weather[weather.columns[i]],errors='coerce')

In [20]:
weather2 =weather.groupby(by =['Year','Month']).mean()
weather2.shape

(60, 20)

In [21]:
weather2.drop("Day",axis=1,inplace=True)

In [22]:
macro.head()

Year-Month  Monthly Nominal GDP Index (inMillion$)  \
0  2009 - Jan                            14421.752895   
1  2009 - Feb                            14389.200466   
2  2009 - Mar                            14340.701639   
3  2009 - Apr                            14326.815525   
4  2009 - May                            14345.904809   

   Monthly Real GDP Index (inMillion$)      CPI PartyInPower  \
0                         14407.053343  233.402    Democrats   
1                         14366.176571  234.663    Democrats   
2                         14351.786822  235.067    Democrats   
3                         14351.601731  235.582    Democrats   
4                         14368.123959  235.975    Democrats   

   unemployment rate  CommercialBankInterestRateonCreditCardPlans  \
0                7.8                                        12.03   
1                8.3                                        12.97   
2                8.7                                        12.97   
3                9.0                                        12.97   
4                9.4                                        13.32   

   Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan  \
0                                              11.44                   
1                                              11.05                   
2                                              11.05                   
3                                              11.05                   
4                                              11.25                   

   Earnings or wages  in dollars per hour  \
0                                   22.05   
1                                   22.22   
2                                   22.22   
3                                   22.13   
4                                   22.04   

  AdvertisingExpenses (in Thousand Dollars)  \
0                                       137   
1                                       200   
2                                         ?   
3                                       214   
4                                         ?   

   Cotton Monthly Price - US cents per Pound(lbs)  Change(in%)  \
0                                           57.70         4.02   
1                                           55.21        -4.32   
2                                           51.50        -6.72   
3                                           56.78        10.25   
4                                           61.95         9.11   

   Average upland planted(million acres)  \
0                                  9.296   
1                                  9.296   
2                                  9.296   
3                                  9.296   
4                                  9.297   

   Average upland harvested(million acres)  yieldperharvested acre  \
0                                    7.559                     799   
1                                    7.559                     799   
2                                    7.559                     799   
3                                    7.559                     787   
4                                    7.400                     803   

   Production (in  480-lb netweright in million bales)  \
0                                             12.589     
1                                             12.589     
2                                             12.589     
3                                             12.400     
4                                             12.384     

   Mill use  (in  480-lb netweright in million bales)  Exports  
0                                               4.17    11.550  
1                                               3.87    11.100  
2                                               3.72    11.650  
3                                               3.62    12.225  
4                                               3.52    12.300

In [23]:
macro['Year-Month']=macro["Year-Month"].astype('datetime64[ns]')

In [24]:
macro["Month"]=macro['Year-Month'].dt.month
macro.head()

Year-Month  Monthly Nominal GDP Index (inMillion$)  \
0 2009-01-01                            14421.752895   
1 2009-02-01                            14389.200466   
2 2009-03-01                            14340.701639   
3 2009-04-01                            14326.815525   
4 2009-05-01                            14345.904809   

   Monthly Real GDP Index (inMillion$)      CPI PartyInPower  \
0                         14407.053343  233.402    Democrats   
1                         14366.176571  234.663    Democrats   
2                         14351.786822  235.067    Democrats   
3                         14351.601731  235.582    Democrats   
4                         14368.123959  235.975    Democrats   

   unemployment rate  CommercialBankInterestRateonCreditCardPlans  \
0                7.8                                        12.03   
1                8.3                                        12.97   
2                8.7                                        12.97   
3                9.0                                        12.97   
4                9.4                                        13.32   

   Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan  \
0                                              11.44                   
1                                              11.05                   
2                                              11.05                   
3                                              11.05                   
4                                              11.25                   

   Earnings or wages  in dollars per hour  \
0                                   22.05   
1                                   22.22   
2                                   22.22   
3                                   22.13   
4                                   22.04   

  AdvertisingExpenses (in Thousand Dollars)  \
0                                       137   
1                                       200   
2                                         ?   
3                                       214   
4                                         ?   

   Cotton Monthly Price - US cents per Pound(lbs)  Change(in%)  \
0                                           57.70         4.02   
1                                           55.21        -4.32   
2                                           51.50        -6.72   
3                                           56.78        10.25   
4                                           61.95         9.11   

   Average upland planted(million acres)  \
0                                  9.296   
1                                  9.296   
2                                  9.296   
3                                  9.296   
4                                  9.297   

   Average upland harvested(million acres)  yieldperharvested acre  \
0                                    7.559                     799   
1                                    7.559                     799   
2                                    7.559                     799   
3                                    7.559                     787   
4                                    7.400                     803   

   Production (in  480-lb netweright in million bales)  \
0                                             12.589     
1                                             12.589     
2                                             12.589     
3                                             12.400     
4                                             12.384     

   Mill use  (in  480-lb netweright in million bales)  Exports  Month  
0                                               4.17    11.550      1  
1                                               3.87    11.100      2  
2                                               3.72    11.650      3  
3                                               3.62    12.225      4  
4                                               3.52    12.300      5

In [25]:
macro["Year"]=macro["Year-Month"].dt.year

In [26]:
macro.isnull().sum()

Year-Month                                                           0
Monthly Nominal GDP Index (inMillion$)                               0
Monthly Real GDP Index (inMillion$)                                  0
CPI                                                                  0
PartyInPower                                                         0
unemployment rate                                                    0
CommercialBankInterestRateonCreditCardPlans                          0
Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan    0
Earnings or wages  in dollars per hour                               0
AdvertisingExpenses (in Thousand Dollars)                            0
Cotton Monthly Price - US cents per Pound(lbs)                       0
Change(in%)                                                          0
Average upland planted(million acres)                                0
Average upland harvested(million acres)                              0
yieldp

In [27]:
macro.head()

Year-Month  Monthly Nominal GDP Index (inMillion$)  \
0 2009-01-01                            14421.752895   
1 2009-02-01                            14389.200466   
2 2009-03-01                            14340.701639   
3 2009-04-01                            14326.815525   
4 2009-05-01                            14345.904809   

   Monthly Real GDP Index (inMillion$)      CPI PartyInPower  \
0                         14407.053343  233.402    Democrats   
1                         14366.176571  234.663    Democrats   
2                         14351.786822  235.067    Democrats   
3                         14351.601731  235.582    Democrats   
4                         14368.123959  235.975    Democrats   

   unemployment rate  CommercialBankInterestRateonCreditCardPlans  \
0                7.8                                        12.03   
1                8.3                                        12.97   
2                8.7                                        12.97   
3                9.0                                        12.97   
4                9.4                                        13.32   

   Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan  \
0                                              11.44                   
1                                              11.05                   
2                                              11.05                   
3                                              11.05                   
4                                              11.25                   

   Earnings or wages  in dollars per hour  \
0                                   22.05   
1                                   22.22   
2                                   22.22   
3                                   22.13   
4                                   22.04   

  AdvertisingExpenses (in Thousand Dollars)  \
0                                       137   
1                                       200   
2                                         ?   
3                                       214   
4                                         ?   

   Cotton Monthly Price - US cents per Pound(lbs)  Change(in%)  \
0                                           57.70         4.02   
1                                           55.21        -4.32   
2                                           51.50        -6.72   
3                                           56.78        10.25   
4                                           61.95         9.11   

   Average upland planted(million acres)  \
0                                  9.296   
1                                  9.296   
2                                  9.296   
3                                  9.296   
4                                  9.297   

   Average upland harvested(million acres)  yieldperharvested acre  \
0                                    7.559                     799   
1                                    7.559                     799   
2                                    7.559                     799   
3                                    7.559                     787   
4                                    7.400                     803   

   Production (in  480-lb netweright in million bales)  \
0                                             12.589     
1                                             12.589     
2                                             12.589     
3                                             12.400     
4                                             12.384     

   Mill use  (in  480-lb netweright in million bales)  Exports  Month  Year  
0                                               4.17    11.550      1  2009  
1                                               3.87    11.100      2  2009  
2                                               3.72    11.650      3  2009  
3                                               3.62    12.225      4  2009  
4                                               3.52    

In [28]:
dfmacro= pd.merge(df,macro,on=['Year','Month'],how='left')
dfmacro.head()

Year  Month ProductCategory  Sales(In ThousandDollars) Year-Month  \
0  2009      1   WomenClothing                     1755.0 2009-01-01   
1  2009      1     MenClothing                      524.0 2009-01-01   
2  2009      1   OtherClothing                      936.0 2009-01-01   
3  2009      2   WomenClothing                     1729.0 2009-02-01   
4  2009      2     MenClothing                      496.0 2009-02-01   

   Monthly Nominal GDP Index (inMillion$)  \
0                            14421.752895   
1                            14421.752895   
2                            14421.752895   
3                            14389.200466   
4                            14389.200466   

   Monthly Real GDP Index (inMillion$)      CPI PartyInPower  \
0                         14407.053343  233.402    Democrats   
1                         14407.053343  233.402    Democrats   
2                         14407.053343  233.402    Democrats   
3                         14366.176571  234.663    Democrats   
4                         14366.176571  234.663    Democrats   

   unemployment rate   ...     Earnings or wages  in dollars per hour  \
0                7.8   ...                                      22.05   
1                7.8   ...                                      22.05   
2                7.8   ...                                      22.05   
3                8.3   ...                                      22.22   
4                8.3   ...                                      22.22   

   AdvertisingExpenses (in Thousand Dollars)  \
0                                        137   
1                                        137   
2                                        137   
3                                        200   
4                                        200   

   Cotton Monthly Price - US cents per Pound(lbs) Change(in%)  \
0                                           57.70        4.02   
1                                           57.70        4.02   
2                                           57.70        4.02   
3                                           55.21       -4.32   
4                                           55.21       -4.32   

   Average upland planted(million acres)  \
0                                  9.296   
1                                  9.296   
2                                  9.296   
3                                  9.296   
4                                  9.296   

   Average upland harvested(million acres)  yieldperharvested acre  \
0                                    7.559                     799   
1                                    7.559                     799   
2                                    7.559                     799   
3                                    7.559                     799   
4                                    7.559                     799   

   Production (in  480-lb netweright in million bales)  \
0                                             12.589     
1                                             12.589     
2                                             12.589     
3                                             12.589     
4                                             12.589     

   Mill use  (in  480-lb netweright in million bales)  Exports  
0                                               4.17     11.55  
1                                               4.17     11.55  
2                                               4.17     11.55  
3                                               3.87     11.10  
4                                               3.87     11.10  

[5 rows x 22 columns]

In [29]:
dfmacro.isnull().sum()

Year                                                                 0
Month                                                                0
ProductCategory                                                      0
Sales(In ThousandDollars)                                            0
Year-Month                                                           0
Monthly Nominal GDP Index (inMillion$)                               0
Monthly Real GDP Index (inMillion$)                                  0
CPI                                                                  0
PartyInPower                                                         0
unemployment rate                                                    0
CommercialBankInterestRateonCreditCardPlans                          0
Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan    0
Earnings or wages  in dollars per hour                               0
AdvertisingExpenses (in Thousand Dollars)                            0
Cotton

In [30]:
dfmacro.shape

(170, 22)

In [31]:
dfmacro.isnull().sum()

Year                                                                 0
Month                                                                0
ProductCategory                                                      0
Sales(In ThousandDollars)                                            0
Year-Month                                                           0
Monthly Nominal GDP Index (inMillion$)                               0
Monthly Real GDP Index (inMillion$)                                  0
CPI                                                                  0
PartyInPower                                                         0
unemployment rate                                                    0
CommercialBankInterestRateonCreditCardPlans                          0
Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan    0
Earnings or wages  in dollars per hour                               0
AdvertisingExpenses (in Thousand Dollars)                            0
Cotton

In [32]:
dfmacro[dfmacro["Year-Month"].isnull()]

Empty DataFrame
Columns: [Year, Month, ProductCategory, Sales(In ThousandDollars), Year-Month, Monthly Nominal GDP Index (inMillion$), Monthly Real GDP Index (inMillion$), CPI, PartyInPower, unemployment rate, CommercialBankInterestRateonCreditCardPlans, Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan, Earnings or wages  in dollars per hour, AdvertisingExpenses (in Thousand Dollars), Cotton Monthly Price - US cents per Pound(lbs), Change(in%), Average upland planted(million acres), Average upland harvested(million acres), yieldperharvested acre, Production (in  480-lb netweright in million bales), Mill use  (in  480-lb netweright in million bales), Exports]
Index: []

[0 rows x 22 columns]

dfmacromonthtest=pd.merge(dfmacrotest,event,on=['Year','Month'],how='outer')
dfmacromonthtest.head()

In [38]:
dfmacromonth=pd.merge(dfmacro,event,on=['Year','Month'],how='left')
dfmacromonth.head()

Year  Month ProductCategory  Sales(In ThousandDollars) Year-Month  \
0  2009      1   WomenClothing                     1755.0 2009-01-01   
1  2009      1   WomenClothing                     1755.0 2009-01-01   
2  2009      1     MenClothing                      524.0 2009-01-01   
3  2009      1     MenClothing                      524.0 2009-01-01   
4  2009      1   OtherClothing                      936.0 2009-01-01   

   Monthly Nominal GDP Index (inMillion$)  \
0                            14421.752895   
1                            14421.752895   
2                            14421.752895   
3                            14421.752895   
4                            14421.752895   

   Monthly Real GDP Index (inMillion$)      CPI PartyInPower  \
0                         14407.053343  233.402    Democrats   
1                         14407.053343  233.402    Democrats   
2                         14407.053343  233.402    Democrats   
3                         14407.053343  233.402    Democrats   
4                         14407.053343  233.402    Democrats   

   unemployment rate ...   Average upland planted(million acres)  \
0                7.8 ...                                   9.296   
1                7.8 ...                                   9.296   
2                7.8 ...                                   9.296   
3                7.8 ...                                   9.296   
4                7.8 ...                                   9.296   

   Average upland harvested(million acres)  yieldperharvested acre  \
0                                    7.559                     799   
1                                    7.559                     799   
2                                    7.559                     799   
3                                    7.559                     799   
4                                    7.559                     799   

  Production (in  480-lb netweright in million bales)  \
0                                             12.589    
1                                             12.589    
2                                             12.589    
3                                             12.589    
4                                             12.589    

   Mill use  (in  480-lb netweright in million bales)  Exports  MonthDate  \
0                                               4.17     11.55 2001-01-01   
1                                               4.17     11.55 2019-01-01   
2                                               4.17     11.55 2001-01-01   
3                                               4.17     11.55 2019-01-01   
4                                               4.17     11.55 2001-01-01   

                        Event      DayCategory  Day  
0              New Year's Day  Federal Holiday  1.0  
1  Martin Luther King Jr. Day  Federal Holiday  1.0  
2              New Year's Day  Federal Holiday  1.0  
3  Martin Luther King Jr. Day  Federal Holiday  1.0  
4              New Year's Day  Federal Holiday  1.0  

[5 rows x 26 columns]

In [ ]:
event.columns

In [34]:
# dfmacromonthtest.drop("Day",axis=1,inplace=True)

In [39]:
print(dfmacro.shape,dfmacromonth.shape)

(170, 22) (293, 26)


In [40]:
dfmacromonth.isnull().sum()

Year                                                                  0
Month                                                                 0
ProductCategory                                                       0
Sales(In ThousandDollars)                                             0
Year-Month                                                            0
Monthly Nominal GDP Index (inMillion$)                                0
Monthly Real GDP Index (inMillion$)                                   0
CPI                                                                   0
PartyInPower                                                          0
unemployment rate                                                     0
CommercialBankInterestRateonCreditCardPlans                           0
Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan     0
Earnings or wages  in dollars per hour                                0
AdvertisingExpenses (in Thousand Dollars)                       

In [41]:
dfmacromonth.drop("Day",axis=1,inplace=True)

In [53]:
# dfmacromonthtest.isnull().sum()

In [42]:
dfmacromonth.drop("MonthDate",axis=1,inplace=True)
# dfmacromonthtest.drop("MonthDate",axis=1,inplace=True)

In [43]:
final=pd.merge(dfmacromonth,weather2,on=['Year','Month'],how='left')
final.head()

Year  Month ProductCategory  Sales(In ThousandDollars) Year-Month  \
0  2009      1   WomenClothing                     1755.0 2009-01-01   
1  2009      1   WomenClothing                     1755.0 2009-01-01   
2  2009      1     MenClothing                      524.0 2009-01-01   
3  2009      1     MenClothing                      524.0 2009-01-01   
4  2009      1   OtherClothing                      936.0 2009-01-01   

   Monthly Nominal GDP Index (inMillion$)  \
0                            14421.752895   
1                            14421.752895   
2                            14421.752895   
3                            14421.752895   
4                            14421.752895   

   Monthly Real GDP Index (inMillion$)      CPI PartyInPower  \
0                         14407.053343  233.402    Democrats   
1                         14407.053343  233.402    Democrats   
2                         14407.053343  233.402    Democrats   
3                         14407.053343  233.402    Democrats   
4                         14407.053343  233.402    Democrats   

   unemployment rate        ...         Sea Level Press. (hPa) high  \
0                7.8        ...                         1021.290323   
1                7.8        ...                         1021.290323   
2                7.8        ...                         1021.290323   
3                7.8        ...                         1021.290323   
4                7.8        ...                         1021.290323   

   Sea Level Press. (hPa) avg  Sea Level Press. (hPa) low  \
0                 1015.967742                 1010.516129   
1                 1015.967742                 1010.516129   
2                 1015.967742                 1010.516129   
3                 1015.967742                 1010.516129   
4                 1015.967742                 1010.516129   

  Visibility (km) high  Visibility (km) avg  Visibility (km) low  \
0                 16.0                 14.0            11.451613   
1                 16.0                 14.0            11.451613   
2                 16.0                 14.0            11.451613   
3                 16.0                 14.0            11.451613   
4                 16.0                 14.0            11.451613   

   Wind (km/h) low  Wind (km/h) avg  Wind (km/h) high  Precip. (mm) sum  
0             27.0             12.0         39.322581          2.803704  
1             27.0             12.0         39.322581          2.803704  
2             27.0             12.0         39.322581          2.803704  
3             27.0             12.0         39.322581          2.803704  
4             27.0             12.0         39.322581          2.803704  

[5 rows x 43 columns]

In [51]:
final.drop_duplicates(inplace=True)
final.shape

(170, 37)

## Applying Models

In [326]:
final.drop(["Dew Point high (°C)","Dew Point low (°C)","Visibility\xa0(km) high","Visibility\xa0(km) low","Temp high (°C)","Temp low (°C)","Humidity\xa0(%) high","Humidity\xa0(%) low","Sea Level Press.\xa0(hPa) high","Sea Level Press.\xa0(hPa) low","Wind\xa0(km/h) high","Wind\xa0(km/h) low"],axis=1,inplace=True)
finaltest.drop(["Dew Point high (°C)","Dew Point low (°C)","Visibility\xa0(km) high","Visibility\xa0(km) low","Temp high (°C)","Temp low (°C)","Humidity\xa0(%) high","Humidity\xa0(%) low","Sea Level Press.\xa0(hPa) high","Sea Level Press.\xa0(hPa) low","Wind\xa0(km/h) high","Wind\xa0(km/h) low"],axis=1,inplace=True)

In [45]:
final.drop(["AdvertisingExpenses (in Thousand Dollars)","PartyInPower","Event","DayCategory"],axis=1,inplace=True)
finaltest.drop(["AdvertisingExpenses (in Thousand Dollars)","PartyInPower","Event","DayCategory"],axis=1,inplace=True)

KeyError: "['AdvertisingExpenses (in Thousand Dollars)' 'PartyInPower' 'Event'\n 'DayCategory'] not found in axis"

In [331]:
# final.drop(["Monthly Real GDP Index (inMillion$)","Production (in  480-lb netweright in million bales)","unemployment rate"],axis=1,inplace=True)
finaltest.drop(["Monthly Real GDP Index (inMillion$)","Temp avg (°C)","Production (in  480-lb netweright in million bales)","unemployment rate"],axis=1,inplace=True)

In [332]:
finaltest.columns

Index(['Year', 'Month', 'ProductCategory',
       'Monthly Nominal GDP Index (inMillion$)', 'CPI',
       'CommercialBankInterestRateonCreditCardPlans',
       'Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan',
       'Earnings or wages  in dollars per hour',
       'Cotton Monthly Price - US cents per Pound(lbs)', 'Change(in%)',
       'Average upland planted(million acres)',
       'Average upland harvested(million acres)', 'yieldperharvested acre',
       'Mill use  (in  480-lb netweright in million bales)', 'Exports',
       'Dew Point avg (°C)', 'Humidity (%) avg', 'Sea Level Press. (hPa) avg',
       'Visibility (km) avg', 'Wind (km/h) avg', 'Precip. (mm) sum'],
      dtype='object')

In [333]:
finaltest.drop(["Earnings or wages  in dollars per hour","Monthly Nominal GDP Index (inMillion$)"],axis=1,inplace=True)
final.drop(["Earnings or wages  in dollars per hour","Monthly Nominal GDP Index (inMillion$)"],axis=1,inplace=True)

KeyError: "['Earnings or wages  in dollars per hour'\n 'Monthly Nominal GDP Index (inMillion$)'] not found in axis"

In [47]:
final.drop("CPI",axis=1,inplace=True)
finaltest.drop("CPI",axis=1,inplace=True)

In [65]:
final.profile_report()

In [52]:
final.shape,finaltest.shape

((170, 37), (36, 36))

In [48]:
final.drop("Year-Month",axis=1,inplace=True)

In [49]:
final.columns

Index(['Year', 'Month', 'ProductCategory', 'Sales(In ThousandDollars)',
       'Monthly Nominal GDP Index (inMillion$)',
       'Monthly Real GDP Index (inMillion$)', 'unemployment rate',
       'CommercialBankInterestRateonCreditCardPlans',
       'Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan',
       'Earnings or wages  in dollars per hour',
       'Cotton Monthly Price - US cents per Pound(lbs)', 'Change(in%)',
       'Average upland planted(million acres)',
       'Average upland harvested(million acres)', 'yieldperharvested acre',
       'Production (in  480-lb netweright in million bales)',
       'Mill use  (in  480-lb netweright in million bales)', 'Exports',
       'Temp high (°C)', 'Temp avg (°C)', 'Temp low (°C)',
       'Dew Point high (°C)', 'Dew Point avg (°C)', 'Dew Point low (°C)',
       'Humidity (%) high', 'Humidity (%) avg', 'Humidity (%) low',
       'Sea Level Press. (hPa) high', 'Sea Level Press. (hPa) avg',
       'Sea Level Press. (hPa) low

In [338]:
finaltest.columns

Index(['Year', 'Month', 'ProductCategory', 'CPI',
       'CommercialBankInterestRateonCreditCardPlans',
       'Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan',
       'Cotton Monthly Price - US cents per Pound(lbs)', 'Change(in%)',
       'Average upland planted(million acres)',
       'Average upland harvested(million acres)', 'yieldperharvested acre',
       'Mill use  (in  480-lb netweright in million bales)', 'Exports',
       'Dew Point avg (°C)', 'Humidity (%) avg', 'Sea Level Press. (hPa) avg',
       'Visibility (km) avg', 'Wind (km/h) avg', 'Precip. (mm) sum'],
      dtype='object')

In [53]:
newfinal=pd.get_dummies(final,drop_first=True)
newfinal.dropna(inplace=True)

# print(train_dummy.shape,test_dummy.shape)
newfinal.columns

Index(['Year', 'Month', 'Sales(In ThousandDollars)',
       'Monthly Nominal GDP Index (inMillion$)',
       'Monthly Real GDP Index (inMillion$)', 'unemployment rate',
       'CommercialBankInterestRateonCreditCardPlans',
       'Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan',
       'Earnings or wages  in dollars per hour',
       'Cotton Monthly Price - US cents per Pound(lbs)', 'Change(in%)',
       'Average upland planted(million acres)',
       'Average upland harvested(million acres)', 'yieldperharvested acre',
       'Production (in  480-lb netweright in million bales)',
       'Mill use  (in  480-lb netweright in million bales)', 'Exports',
       'Temp high (°C)', 'Temp avg (°C)', 'Temp low (°C)',
       'Dew Point high (°C)', 'Dew Point avg (°C)', 'Dew Point low (°C)',
       'Humidity (%) high', 'Humidity (%) avg', 'Humidity (%) low',
       'Sea Level Press. (hPa) high', 'Sea Level Press. (hPa) avg',
       'Sea Level Press. (hPa) low', 'Visibility (km)

In [60]:
X=newfinal.drop('Sales(In ThousandDollars)',axis=1)
Y=newfinal['Sales(In ThousandDollars)']
xtrain,xtest,ytrain,ytest = train_test_split(X,Y,test_size=0.20)

In [61]:
print(xtrain.shape,xtest.shape,ytrain.shape,ytest.shape)

(136, 37) (34, 37) (136,) (34,)


In [62]:
newfinal.shape,dummy.shape

((170, 38), (36, 37))

In [63]:
dummy=pd.get_dummies(finaltest,drop_first=True)
dummy.shape
dummy.columns

Index(['Year', 'Month', 'Monthly Nominal GDP Index (inMillion$)',
       'Monthly Real GDP Index (inMillion$)', 'unemployment rate',
       'CommercialBankInterestRateonCreditCardPlans',
       'Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan',
       'Earnings or wages  in dollars per hour',
       'Cotton Monthly Price - US cents per Pound(lbs)', 'Change(in%)',
       'Average upland planted(million acres)',
       'Average upland harvested(million acres)', 'yieldperharvested acre',
       'Production (in  480-lb netweright in million bales)',
       'Mill use  (in  480-lb netweright in million bales)', 'Exports',
       'Temp high (°C)', 'Temp avg (°C)', 'Temp low (°C)',
       'Dew Point high (°C)', 'Dew Point avg (°C)', 'Dew Point low (°C)',
       'Humidity (%) high', 'Humidity (%) avg', 'Humidity (%) low',
       'Sea Level Press. (hPa) high', 'Sea Level Press. (hPa) avg',
       'Sea Level Press. (hPa) low', 'Visibility (km) high',
       'Visibility (km) avg'

In [59]:
lr=LinearRegression()
lr.fit(xtrain,ytrain)
pred=lr.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))
print(r2_score(ytest,pred))


393.220445163366
0.8895244195601326


In [345]:
lr=Ridge()
lr.fit(xtrain,ytrain)
pred=lr.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))
print(r2_score(ytest,pred))

387.33025606785577
0.8918062657271296


In [197]:
from sklearn.decomposition import PCA
pca=PCA(n_components=2)
xtrain=pca.fit_transform(xtrain,ytrain)
xtest=pca.transform(xtest)
# dummy=pca.transform(dummy)
pca.explained_variance_ratio_

array([0.99543412, 0.00245316])

In [248]:
dt=DecisionTreeRegressor(random_state=1)
dt.fit(xtrain,ytrain)
pred=dt.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))
print(r2_score(ytest,pred))



204.30333560952076
0.9672659204384395


In [347]:
svr=SVR(kernel='linear',degree=3)
svr.fit(xtrain,ytrain)
pred=svr.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))
print(r2_score(ytest,pred))



1352.5637825228591
-0.3193340559838209


In [ ]:
import xgboost as xgb
xgb_model = xgb.XGBRegressor(max_depth=2,n_estimators=50)
xgb_model.fit(xtrain,ytrain)
pred=xgb_model.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))

In [64]:
for k in range(1,20):
    rf=RandomForestRegressor(n_estimators=k,random_state=1)
    rf.fit(xtrain,ytrain)
    pred=rf.predict(xtest)
    print(k,"score",r2_score(ytest,pred),"error",np.sqrt(mean_squared_error(ytest,pred)))

1 score 0.8951333582919785 error 376.34769593461596
2 score 0.8810531393670482 error 400.8178679092215
3 score 0.8889608430708597 error 387.26536645081956
4 score 0.8839698956668802 error 395.8730369664734
5 score 0.8927169586902791 error 380.65901523851096
6 score 0.9046745258895691 error 358.8187000103593
7 score 0.9067832078218414 error 354.82781614699354
8 score 0.901685771103918 error 364.4003371273542
9 score 0.9125881532949874 error 343.6020364857057
10 score 0.9043297281059327 error 359.46704831393015
11 score 0.902205414292062 error 363.4360360630026
12 score 0.8999340139649222 error 367.6324352320406
13 score 0.8995479495567035 error 368.3409335581556
14 score 0.8938855538435968 error 378.58014854393593
15 score 0.899198236813435 error 368.98154567098834
16 score 0.9026679722404392 error 362.5755104860613
17 score 0.904909805717747 error 358.37561299823165
18 score 0.9083604652521661 error 351.8131101965543
19 score 0.9079768099421428 error 352.54878608496915


In [65]:
rf=RandomForestRegressor(n_estimators=18,random_state=1)
rfmodel=rf.fit(xtrain,ytrain)
pred=rf.predict(xtest)
print("score",r2_score(ytest,pred),"error",np.sqrt(mean_squared_error(ytest,pred)))
test_predictions = rfmodel.predict(dummy)
solution = pd.DataFrame({"Year":range(1,37),
                         "Sales(In ThousandDollars)":test_predictions})
solution.to_csv("rf-macro.csv",index=False)

score 0.9083604652521661 error 351.8131101965543


In [186]:
len(pred)

30

In [169]:
xtest.head()

Year  Month  Monthly Nominal GDP Index (inMillion$)  \
220  2013      1                            16503.915684   
75   2010      6                            14945.570371   
66   2010      4                            14844.531193   
242  2013      7                            16685.742246   
241  2013      7                            16685.742246   

     Monthly Real GDP Index (inMillion$)      CPI  unemployment rate  \
220                         15554.426878  254.807                8.0   
75                          14772.318051  240.817                9.4   
66                          14724.200153  240.529                9.9   
242                         15606.008068  257.326                7.3   
241                         15606.008068  257.326                7.3   

     CommercialBankInterestRateonCreditCardPlans  \
220                                        11.88   
75                                         13.84   
66                                         14.26   
242                                        11.95   
241                                        11.95   

     Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan  \
220                                              10.64                   
75                                               11.00                   
66                                               10.83                   
242                                              10.34                   
241                                              10.34                   

     Earnings or wages  in dollars per hour  \
220                                   23.88   
75                                    22.34   
66                                    22.53   
242                                   23.81   
241                                   23.81   

     Cotton Monthly Price - US cents per Pound(lbs)  \
220                                           85.51   
75                                            91.68   
66                                            88.09   
242                                           92.62   
241                                           92.62   

                 ...                Sea Level Press. (hPa) low  \
220              ...                               1014.838710   
75               ...                               1009.066667   
66               ...                               1010.100000   
242              ...                               1014.419355   
241              ...                               1014.419355   

     Visibility (km) high  Visibility (km) avg  Visibility (km) low  \
220             15.741935            13.258065            10.161290   
75              16.000000            14.233333            10.333333   
66              16.000000            14.466667            11.633333   
242             15.645161            13.129032             9.032258   
241             15.645161            13.129032             9.032258   

     Wind (km/h) low  Wind (km/h) avg  Wind (km/h) high  Precip. (mm) sum  \
220        24.903226        10.322581         39.193548          2.417931   
75         21.700000         8.000000         32.033333          1.995714   
66         23.766667        10.200000         35.566667          2.712143   
242        20.387097         7.000000         32.935484          2.486897   
241        20.387097         7.000000         32.935484          2.486897   

     ProductCategory_OtherClothing  ProductCategory_WomenClothing  
220                              1                              0  
75                               1                              0  
66                               0                              0  
242                              1                              0  
241                              0                              0  

[5 rows x 38 columns]

In [141]:
xtest.reset_index(inplace=True)

In [66]:
import xgboost as xgb
xgb_model = xgb.XGBRegressor(n_estimators=400)
xgb_model.fit(xtrain,ytrain)
pred=xgb_model.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))
testdata = finaltest
test_predictions = xgb_model.predict(dummy)
solution = pd.DataFrame({"Year":range(1,37),
                         "Sales(In ThousandDollars)":test_predictions})
solution.to_csv("xgb-macro.csv",index=False)

C:\Users\SURBHI\Anaconda3\lib\site-packages\xgboost\core.py:587: FutureWarning: Series.base is deprecated and will be removed in a future version
  if getattr(data, 'base', None) is not None and \


[22:00:58] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
249.86053216663797


In [170]:
from sklearn.model_selection import GridSearchCV
parameters = {'n_estimators':range(1,20) }
gd=GridSearchCV(rf , param_grid=parameters)
gd.fit(xtrain,ytrain)
gd.best_params_

{'n_estimators': 19}

In [155]:
from sklearn.linear_model import ElasticNet

e=ElasticNet(alpha=1,random_state=123)
pred_elastic=e.fit(xtrain,ytrain).predict(xtest)
print(r2_score(ytest,pred_elastic))
print(np.sqrt(mean_squared_error(ytest,pred_elastic)))

0.3464312994358383
909.4108011692616


In [ ]:
pd.DataFrame({"Year":})

In [100]:
final.shape,finaltest.shape

((170, 19), (36, 18))

Index(['Year', 'Month', 'CommercialBankInterestRateonCreditCardPlans',
       'Finance Rate on Personal Loans at Commercial Banks, 24 Month Loan',
       'Cotton Monthly Price - US cents per Pound(lbs)', 'Change(in%)',
       'Average upland planted(million acres)',
       'Average upland harvested(million acres)', 'yieldperharvested acre',
       'Mill use  (in  480-lb netweright in million bales)', 'Exports',
       'Dew Point avg (°C)', 'Humidity (%) avg', 'Sea Level Press. (hPa) avg',
       'Visibility (km) avg', 'Wind (km/h) avg', 'Precip. (mm) sum',
       'ProductCategory_OtherClothing', 'ProductCategory_WomenClothing'],
      dtype='object')

In [157]:

rf=RandomForestRegressor(n_estimators=1,random_state=1)
rfmodel=rf.fit(xtrain,ytrain)
pred=rf.predict(xtest)
print("score",r2_score(ytest,pred),"error",np.sqrt(mean_squared_error(ytest,pred)))

testdata = finaltest
test_predictions = rfmodel.predict(dummy)
solution = pd.DataFrame({"Year":range(1,37),
                         "Sales(In ThousandDollars)":test_predictions})
solution.to_csv("randomforest-macro.csv",index=False)

score 0.9130225463674378 error 331.7552694736429


In [102]:
import xgboost as xgb
xgb_model = xgb.XGBRegressor(n_estimators=300)
xg=xgb_model.fit(xtrain,ytrain)
pred=xgb_model.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))

from sklearn.model_selection import GridSearchCV
parameters = {'n_estimators':[100,200,300,400,500,600] }
gd=GridSearchCV(xgb_model , param_grid=parameters)
gd.fit(xtrain,ytrain)
print(gd.best_params_)


[18:15:29] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
127.17114620329129
[18:15:29] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[18:15:29] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[18:15:29] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[18:15:30] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
[18:15:30] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederro

In [175]:
xgb_model = xgb.XGBRegressor(n_estimators=600)
xg=xgb_model.fit(xtrain,ytrain)
pred=xgb_model.predict(xtest)
print(np.sqrt(mean_squared_error(ytest,pred)))

[18:40:04] WARNING: C:/Jenkins/workspace/xgboost-win64_release_0.90/src/objective/regression_obj.cu:152: reg:linear is now deprecated in favor of reg:squarederror.
144.8529138991872


In [625]:
print(gd.best_params_)

{'n_estimators': 19}


In [78]:
testdata = finaltest
test_predictions = xg.predict(dummy)
solution = pd.DataFrame({"Year":range(1,37),
                         "Sales(In ThousandDollars)":test_predictions})
solution.to_csv("xgboost-macro.csv",index=False)

NameError: name 'xg' is not defined